In [1]:
#@title set font and wrap
from IPython.display import HTML, display

def set_css():
  display(HTML('''
  <style>
    pre {
        white-space: pre-wrap;
    }
  </style>
  '''))
get_ipython().events.register('pre_run_cell', set_css)

In [ ]:
#!git clone https://github.com/yuangan/EAT_code.git
!wget https://huggingface.co./waveydaveygravy/styletalk/resolve/main/EAT_code.zip
!unzip /content/EAT_code.zip
%cd /content/EAT_code
!pip install -r requirements.txt
!pip install resampy
#!pip install face_detection
!pip install python_speech_features
#@title make directories if not done yet
!mkdir tensorflow
!mkdir Results
!mkdir ckpt
!mkdir demo
!mkdir Utils
%cd /content/EAT_code/tensorflow
!mkdir models
%cd /content/EAT_code
print("done")

In [ ]:
#@title in /content/EAT_code/config/deepprompt_eam3d_st_tanh_304_3090_all.yaml change batch_size to 1 line 70

In [ ]:
#@title make directories if not done yet
!mkdir tensorflow
!mkdir ckpt
!mkdir demo
!mkdir Utils
%cd /content/EAT_code/demo
!mkdir imgs1
!mkdir imgs_cropped1
!mkdir imgs_latent1
%cd /content/EAT_code/tensorflow
!mkdir models
%cd /content/EAT_code

In [ ]:
#@title donwload and place deepspeech model
%cd /content/EAT_code
!gdown --id 1KK15n2fOdfLECWN5wvX54mVyDt18IZCo && unzip -q ckpt.zip -d ckpt
!gdown --id 1MeFGC7ig-vgpDLdhh2vpTIiElrhzZmgT && unzip -q demo.zip -d demo
!gdown --id 1HGVzckXh-vYGZEUUKMntY1muIbkbnRcd && unzip -q Utils.zip -d Utils
%cd /content/EAT_code/tensorflow/models
!wget https://github.com/osmr/deepspeech_features/releases/download/v0.0.1/deepspeech-0_1_0-b90017e8.pb.zip
%cd /content/EAT_code

In [ ]:
#@title download models
%cd /content/EAT_code

!gdown --id 1KK15n2fOdfLECWN5wvX54mVyDt18IZCo && unzip -q ckpt.zip -d ckpt
!gdown --id 1MeFGC7ig-vgpDLdhh2vpTIiElrhzZmgT && unzip -q demo.zip -d demo
!gdown --id 1HGVzckXh-vYGZEUUKMntY1muIbkbnRcd && unzip -q Utils.zip -d Utils

In [5]:
#@title upload custom mp4 to videos
%cd /content/EAT_code/preprocess/video
from google.colab import files
uploaded = files.upload()
%cd /content/EAT_code

/content/EAT_code/preprocess/video


Saving bo_1resized.mp4 to bo_1resized.mp4
/content/EAT_code


In [ ]:
#@title extract boundary boxes
!python /content/EAT_code/preprocess/extract_bbox.py

In [ ]:
#@title place custom video in preprocess/video
%cd /content/EAT_code/preprocess
!python /content/EAT_code/preprocess/preprocess_video.py # --deepspeech "/content/EAT_code/tensorflow/models/deepspeech-0_1_0-b90017e8.pb"

In [ ]:
        print(f"Number of paths: {len(self.A_paths)}")
        print("Paths:")
        for path in self.A_paths:
            print(path)

In [ ]:
import numpy as np

# Replace "path/to/your/file.npy" with the actual path to your file
data = np.load("/content/EAT_code/demo/video_processed/obama/latent_evp_25/obama.npy")

print(f"Type: {type(data)}")
print(f"Shape: {data.shape}")

In [14]:
!python /content/EAT_code/demo.py --root_wav /content/EAT_code/demo/video_processed1/bo_1resized --emo ang --save_dir /content/EAT_code/Results

deepprompt_eam3d_all_final_313
cuda is available
/usr/local/lib/python3.10/dist-packages/torch/functional.py:568: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ../aten/src/ATen/native/TensorShape.cpp:2228.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]
  0% 0/1 [00:00<?, ?it/s]
  0% 0/1 [00:00<?, ?it/s]/content/EAT_code/modules/model_transformer.py:158: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  pred = F.softmax(pred)


  0% 0/177 [00:00<?, ?it/s]/usr/local/lib/python3.10/dist-packages/torch/nn/functional.py:4193: UserWarning: Default grid_sample and affine_grid behavior has changed to align_corners=False since 1.3.0. Please specify align_corners=True if the old behavior is desired. See the documentation of grid_sample for details.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/torch/nn/fun

In [ ]:
%cd /content
!zip -r EAT_code.zip /EAT_code

In [ ]:
#@title demo.py with fixed paths

import os
import numpy as np
import torch
import yaml
from modules.generator import OcclusionAwareSPADEGeneratorEam
from modules.keypoint_detector import KPDetector, HEEstimator
import argparse
import imageio
from modules.transformer import Audio2kpTransformerBBoxQDeepPrompt as Audio2kpTransformer
from modules.prompt import EmotionDeepPrompt, EmotionalDeformationTransformer
from scipy.io import wavfile

from modules.model_transformer import get_rotation_matrix, keypoint_transformation
from skimage import io, img_as_float32
from skimage.transform import resize
import torchaudio
import soundfile as sf
from scipy.spatial import ConvexHull

import torch.nn.functional as F
import glob
from tqdm import tqdm
import gzip

emo_label = ['ang',  'con',  'dis',  'fea',  'hap',  'neu',  'sad',  'sur']
emo_label_full = ['angry',  'contempt',  'disgusted',  'fear',  'happy',  'neutral',  'sad',  'surprised']
latent_dim = 16

MEL_PARAMS_25 = {
    "n_mels": 80,
    "n_fft": 2048,
    "win_length": 640,
    "hop_length": 640
}

to_melspec = torchaudio.transforms.MelSpectrogram(**MEL_PARAMS_25)
mean, std = -4, 4

expU = torch.from_numpy(np.load('/content/EAT_code/expPCAnorm_fin/U_mead.npy')[:,:32])
expmean = torch.from_numpy(np.load('/content/EAT_code/expPCAnorm_fin/mean_mead.npy'))

root_wav = './demo/video_processed/M003_neu_1_001'
def normalize_kp(kp_source, kp_driving, kp_driving_initial,
                 use_relative_movement=True, use_relative_jacobian=True):

    kp_new = {k: v for k, v in kp_driving.items()}
    if use_relative_movement:
        kp_value_diff = (kp_driving['value'] - kp_driving_initial['value'])
        kp_new['value'] = kp_value_diff + kp_source['value']

        if use_relative_jacobian:
            jacobian_diff = torch.matmul(kp_driving['jacobian'], torch.inverse(kp_driving_initial['jacobian']))
            kp_new['jacobian'] = torch.matmul(jacobian_diff, kp_source['jacobian'])

    return kp_new

def _load_tensor(data):
    wave_path = data
    wave, sr = sf.read(wave_path)
    wave_tensor = torch.from_numpy(wave).float()
    return wave_tensor

def build_model(config, device_ids=[0]):
    generator = OcclusionAwareSPADEGeneratorEam(**config['model_params']['generator_params'],
                                                 **config['model_params']['common_params'])
    if torch.cuda.is_available():
        print('cuda is available')
        generator.to(device_ids[0])

    kp_detector = KPDetector(**config['model_params']['kp_detector_params'],
                             **config['model_params']['common_params'])

    if torch.cuda.is_available():
        kp_detector.to(device_ids[0])


    audio2kptransformer = Audio2kpTransformer(**config['model_params']['audio2kp_params'], face_ea=True)

    if torch.cuda.is_available():
        audio2kptransformer.to(device_ids[0])

    sidetuning = EmotionalDeformationTransformer(**config['model_params']['audio2kp_params'])

    if torch.cuda.is_available():
        sidetuning.to(device_ids[0])

    emotionprompt = EmotionDeepPrompt()

    if torch.cuda.is_available():
        emotionprompt.to(device_ids[0])

    return generator, kp_detector, audio2kptransformer, sidetuning, emotionprompt


def prepare_test_data(img_path, audio_path, opt, emotype, use_otherimg=True):
    # sr,_ = wavfile.read(audio_path)

    if use_otherimg:
        source_latent = np.load(img_path.replace('cropped', 'latent')[:-4]+'.npy', allow_pickle=True)
    else:
        source_latent = np.load(img_path.replace('images', 'latent')[:-9]+'.npy', allow_pickle=True)
    he_source = {}
    for k in source_latent[1].keys():
        he_source[k] = torch.from_numpy(source_latent[1][k][0]).unsqueeze(0).cuda()

    # source images
    source_img = img_as_float32(io.imread(img_path)).transpose((2, 0, 1))
    asp = os.path.basename(audio_path)[:-4]

    # latent code
    y_trg = emo_label.index(emotype)
    z_trg = torch.randn(latent_dim)

    # driving latent
    latent_path_driving = f'{root_wav}/latent_evp_25/{asp}.npy'
    pose_gz = gzip.GzipFile(f'{root_wav}/poseimg/{asp}.npy.gz', 'r')
    poseimg = np.load(pose_gz)
    deepfeature = np.load(f'{root_wav}/deepfeature32/{asp}.npy')
    driving_latent = np.load(latent_path_driving[:-4]+'.npy', allow_pickle=True)
    he_driving = driving_latent[1]

    # gt frame number
    frames = glob.glob(f'{root_wav}/images_evp_25/cropped/*.jpg')
    num_frames = len(frames)

    wave_tensor = _load_tensor(audio_path)
    if len(wave_tensor.shape) > 1:
        wave_tensor = wave_tensor[:, 0]
    mel_tensor = to_melspec(wave_tensor)
    mel_tensor = (torch.log(1e-5 + mel_tensor) - mean) / std
    name_len = min(mel_tensor.shape[1], poseimg.shape[0], deepfeature.shape[0])

    audio_frames = []
    poseimgs = []
    deep_feature = []

    pad, deep_pad = np.load('pad.npy', allow_pickle=True)

    if name_len < num_frames:
        diff = num_frames - name_len
        if diff > 2:
            print(f"Attention: the frames are {diff} more than name_len, we will use name_len to replace num_frames")
            num_frames=name_len
            for k in he_driving.keys():
                he_driving[k] = he_driving[k][:name_len, :]
    for rid in range(0, num_frames):
        audio = []
        poses = []
        deeps = []
        for i in range(rid - opt['num_w'], rid + opt['num_w'] + 1):
            if i < 0:
                audio.append(pad)
                poses.append(poseimg[0])
                deeps.append(deep_pad)
            elif i >= name_len:
                audio.append(pad)
                poses.append(poseimg[-1])
                deeps.append(deep_pad)
            else:
                audio.append(mel_tensor[:, i])
                poses.append(poseimg[i])
                deeps.append(deepfeature[i])

        audio_frames.append(torch.stack(audio, dim=1))
        poseimgs.append(poses)
        deep_feature.append(deeps)
    audio_frames = torch.stack(audio_frames, dim=0)
    poseimgs = torch.from_numpy(np.array(poseimgs))
    deep_feature = torch.from_numpy(np.array(deep_feature)).to(torch.float)
    return audio_frames, poseimgs, deep_feature, source_img, he_source, he_driving, num_frames, y_trg, z_trg, latent_path_driving

def load_ckpt(ckpt, kp_detector, generator, audio2kptransformer, sidetuning, emotionprompt):
    checkpoint = torch.load(ckpt, map_location=torch.device('cpu'))
    if audio2kptransformer is not None:
        audio2kptransformer.load_state_dict(checkpoint['audio2kptransformer'])
    if generator is not None:
        generator.load_state_dict(checkpoint['generator'])
    if kp_detector is not None:
        kp_detector.load_state_dict(checkpoint['kp_detector'])
    if sidetuning is not None:
        sidetuning.load_state_dict(checkpoint['sidetuning'])
    if emotionprompt is not None:
        emotionprompt.load_state_dict(checkpoint['emotionprompt'])

import cv2
import dlib
from tqdm import tqdm
from skimage import transform as tf
detector = dlib.get_frontal_face_detector()
predictor = dlib.shape_predictor('/content/EAT_code/demo/shape_predictor_68_face_landmarks.dat')

def shape_to_np(shape, dtype="int"):
    # initialize the list of (x, y)-coordinates
    coords = np.zeros((shape.num_parts, 2), dtype=dtype)

    # loop over all facial landmarks and convert them
    # to a 2-tuple of (x, y)-coordinates
    for i in range(0, shape.num_parts):
        coords[i] = (shape.part(i).x, shape.part(i).y)

    # return the list of (x, y)-coordinates
    return coords

def crop_image(image_path, out_path):
    template = np.load('./demo/M003_template.npy')
    image = cv2.imread(image_path)
    gray = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    rects = detector(gray, 1)  #detect human face
    if len(rects) != 1:
        return 0
    for (j, rect) in enumerate(rects):
        shape = predictor(gray, rect) #detect 68 points
        shape = shape_to_np(shape)

    pts2 = np.float32(template[:47,:])
    pts1 = np.float32(shape[:47,:]) #eye and nose
    tform = tf.SimilarityTransform()
    tform.estimate( pts2, pts1) #Set the transformation matrix with the explicit parameters.

    dst = tf.warp(image, tform, output_shape=(256, 256))

    dst = np.array(dst * 255, dtype=np.uint8)

    cv2.imwrite(out_path, dst)

def preprocess_imgs(allimgs, tmp_allimgs_cropped):
    name_cropped = []
    for path in tmp_allimgs_cropped:
        name_cropped.append(os.path.basename(path))
    for path in allimgs:
        if os.path.basename(path) in name_cropped:
            continue
        else:
            out_path = path.replace('imgs/', 'imgs_cropped/')
            crop_image(path, out_path)

from sync_batchnorm import DataParallelWithCallback
def load_checkpoints_extractor(config_path, checkpoint_path, cpu=False):

    with open(config_path) as f:
        config = yaml.load(f, Loader=yaml.FullLoader)

    kp_detector = KPDetector(**config['model_params']['kp_detector_params'],
                             **config['model_params']['common_params'])
    if not cpu:
        kp_detector.cuda()

    he_estimator = HEEstimator(**config['model_params']['he_estimator_params'],
                               **config['model_params']['common_params'])
    if not cpu:
        he_estimator.cuda()

    if cpu:
        checkpoint = torch.load(checkpoint_path, map_location=torch.device('cpu'))
    else:
        checkpoint = torch.load(checkpoint_path)

    kp_detector.load_state_dict(checkpoint['kp_detector'])
    he_estimator.load_state_dict(checkpoint['he_estimator'])

    if not cpu:
        kp_detector = DataParallelWithCallback(kp_detector)
        he_estimator = DataParallelWithCallback(he_estimator)

    kp_detector.eval()
    he_estimator.eval()

    return kp_detector, he_estimator

def estimate_latent(driving_video, kp_detector, he_estimator):
    with torch.no_grad():
        predictions = []
        driving = torch.tensor(np.array(driving_video)[np.newaxis].astype(np.float32)).permute(0, 4, 1, 2, 3).cuda()
        kp_canonical = kp_detector(driving[:, :, 0])
        he_drivings = {'yaw': [], 'pitch': [], 'roll': [], 't': [], 'exp': []}

        for frame_idx in range(driving.shape[2]):
            driving_frame = driving[:, :, frame_idx]
            he_driving = he_estimator(driving_frame)
            for k in he_drivings.keys():
                he_drivings[k].append(he_driving[k])
    return [kp_canonical, he_drivings]

def extract_keypoints(extract_list):
    kp_detector, he_estimator = load_checkpoints_extractor(config_path='config/vox-256-spade.yaml', checkpoint_path='./ckpt/pretrain_new_274.pth.tar')
    if not os.path.exists('./demo/imgs_latent/'):
        os.makedirs('./demo/imgs_latent/')
    for imgname in tqdm(extract_list):
        path_frames = [imgname]
        filesname=os.path.basename(imgname)[:-4]
        if os.path.exists(f'./demo/imgs_latent/'+filesname+'.npy'):
            continue
        driving_frames = []
        for im in path_frames:
            driving_frames.append(imageio.imread(im))
        driving_video = [resize(frame, (256, 256))[..., :3] for frame in driving_frames]

        kc, he = estimate_latent(driving_video, kp_detector, he_estimator)
        kc = kc['value'].cpu().numpy()
        for k in he:
            he[k] = torch.cat(he[k]).cpu().numpy()
        np.save('./demo/imgs_latent/'+filesname, [kc, he])

def preprocess_cropped_imgs(allimgs_cropped):
    extract_list = []
    for img_path in allimgs_cropped:
        if not os.path.exists(img_path.replace('cropped', 'latent')[:-4]+'.npy'):
            extract_list.append(img_path)
    if len(extract_list) > 0:
        print('=========', "Extract latent keypoints from New image", '======')
        extract_keypoints(extract_list)

def test(ckpt, emotype, save_dir=" "):
    # with open("config/vox-transformer2.yaml") as f:
    with open("/content/EAT_code/config/deepprompt_eam3d_st_tanh_304_3090_all.yaml") as f:
        config = yaml.load(f, Loader=yaml.FullLoader)
    cur_path = os.getcwd()
    generator, kp_detector, audio2kptransformer, sidetuning, emotionprompt = build_model(config)
    load_ckpt(ckpt, kp_detector=kp_detector, generator=generator, audio2kptransformer=audio2kptransformer, sidetuning=sidetuning, emotionprompt=emotionprompt)

    audio2kptransformer.eval()
    generator.eval()
    kp_detector.eval()
    sidetuning.eval()
    emotionprompt.eval()

    all_wavs2 = [f'{root_wav}/{os.path.basename(root_wav)}.wav']
    allimg = glob.glob('./demo/imgs/*.jpg')
    tmp_allimg_cropped = glob.glob('./demo/imgs_cropped/*.jpg')
    preprocess_imgs(allimg, tmp_allimg_cropped) # crop and align images

    allimg_cropped = glob.glob('./demo/imgs_cropped/*.jpg')
    preprocess_cropped_imgs(allimg_cropped) # extract latent keypoints if necessary

    for ind in tqdm(range(len(all_wavs2))):
        for img_path in tqdm(allimg_cropped):
            audio_path = all_wavs2[ind]
            # read in data
            audio_frames, poseimgs, deep_feature, source_img, he_source, he_driving, num_frames, y_trg, z_trg, latent_path_driving = prepare_test_data(img_path, audio_path, config['model_params']['audio2kp_params'], emotype)


            with torch.no_grad():
                source_img = torch.from_numpy(source_img).unsqueeze(0).cuda()
                kp_canonical = kp_detector(source_img, with_feature=True)     # {'value': value, 'jacobian': jacobian}
                kp_cano = kp_canonical['value']

                x = {}
                x['mel'] = audio_frames.unsqueeze(1).unsqueeze(0).cuda()
                x['z_trg'] = z_trg.unsqueeze(0).cuda()
                x['y_trg'] = torch.tensor(y_trg, dtype=torch.long).cuda().reshape(1)
                x['pose'] = poseimgs.cuda()
                x['deep'] = deep_feature.cuda().unsqueeze(0)
                x['he_driving'] = {'yaw': torch.from_numpy(he_driving['yaw']).cuda().unsqueeze(0),
                                'pitch': torch.from_numpy(he_driving['pitch']).cuda().unsqueeze(0),
                                'roll': torch.from_numpy(he_driving['roll']).cuda().unsqueeze(0),
                                't': torch.from_numpy(he_driving['t']).cuda().unsqueeze(0),
                                }

                ### emotion prompt
                emoprompt, deepprompt = emotionprompt(x)
                a2kp_exps = []
                emo_exps = []
                T = 5
                if T == 1:
                    for i in range(x['mel'].shape[1]):
                        xi = {}
                        xi['mel'] = x['mel'][:,i,:,:,:].unsqueeze(1)
                        xi['z_trg'] = x['z_trg']
                        xi['y_trg'] = x['y_trg']
                        xi['pose'] = x['pose'][i,:,:,:,:].unsqueeze(0)
                        xi['deep'] = x['deep'][:,i,:,:,:].unsqueeze(1)
                        xi['he_driving'] = {'yaw': x['he_driving']['yaw'][:,i,:].unsqueeze(0),
                                    'pitch': x['he_driving']['pitch'][:,i,:].unsqueeze(0),
                                    'roll': x['he_driving']['roll'][:,i,:].unsqueeze(0),
                                    't': x['he_driving']['t'][:,i,:].unsqueeze(0),
                                    }
                        he_driving_emo_xi, input_st_xi = audio2kptransformer(xi, kp_canonical, emoprompt=emoprompt, deepprompt=deepprompt, side=True)           # {'yaw': yaw, 'pitch': pitch, 'roll': roll, 't': t, 'exp': exp}
                        emo_exp = sidetuning(input_st_xi, emoprompt, deepprompt)
                        a2kp_exps.append(he_driving_emo_xi['emo'])
                        emo_exps.append(emo_exp)
                elif T is not None:
                    for i in range(x['mel'].shape[1]//T+1):
                        if i*T >= x['mel'].shape[1]:
                            break
                        xi = {}
                        xi['mel'] = x['mel'][:,i*T:(i+1)*T,:,:,:]
                        xi['z_trg'] = x['z_trg']
                        xi['y_trg'] = x['y_trg']
                        xi['pose'] = x['pose'][i*T:(i+1)*T,:,:,:,:]
                        xi['deep'] = x['deep'][:,i*T:(i+1)*T,:,:,:]
                        xi['he_driving'] = {'yaw': x['he_driving']['yaw'][:,i*T:(i+1)*T,:],
                                    'pitch': x['he_driving']['pitch'][:,i*T:(i+1)*T,:],
                                    'roll': x['he_driving']['roll'][:,i*T:(i+1)*T,:],
                                    't': x['he_driving']['t'][:,i*T:(i+1)*T,:],
                                    }
                        he_driving_emo_xi, input_st_xi = audio2kptransformer(xi, kp_canonical, emoprompt=emoprompt, deepprompt=deepprompt, side=True)           # {'yaw': yaw, 'pitch': pitch, 'roll': roll, 't': t, 'exp': exp}
                        emo_exp = sidetuning(input_st_xi, emoprompt, deepprompt)
                        a2kp_exps.append(he_driving_emo_xi['emo'])
                        emo_exps.append(emo_exp)

                if T is None:
                    he_driving_emo, input_st = audio2kptransformer(x, kp_canonical, emoprompt=emoprompt, deepprompt=deepprompt, side=True)           # {'yaw': yaw, 'pitch': pitch, 'roll': roll, 't': t, 'exp': exp}
                    emo_exps = sidetuning(input_st, emoprompt, deepprompt).reshape(-1, 45)
                else:
                    he_driving_emo = {}
                    he_driving_emo['emo'] = torch.cat(a2kp_exps, dim=0)
                    emo_exps = torch.cat(emo_exps, dim=0).reshape(-1, 45)

                exp = he_driving_emo['emo']
                device = exp.get_device()
                exp = torch.mm(exp, expU.t().to(device))
                exp = exp + expmean.expand_as(exp).to(device)
                exp = exp + emo_exps


                source_area = ConvexHull(kp_cano[0].cpu().numpy()).volume
                exp = exp * source_area

                he_new_driving = {'yaw': torch.from_numpy(he_driving['yaw']).cuda(),
                                'pitch': torch.from_numpy(he_driving['pitch']).cuda(),
                                'roll': torch.from_numpy(he_driving['roll']).cuda(),
                                't': torch.from_numpy(he_driving['t']).cuda(),
                                'exp': exp}
                he_driving['exp'] = torch.from_numpy(he_driving['exp']).cuda()

                kp_source = keypoint_transformation(kp_canonical, he_source, False)
                mean_source = torch.mean(kp_source['value'], dim=1)[0]
                kp_driving = keypoint_transformation(kp_canonical, he_new_driving, False)
                mean_driving = torch.mean(torch.mean(kp_driving['value'], dim=1), dim=0)
                kp_driving['value'] = kp_driving['value']+(mean_source-mean_driving).unsqueeze(0).unsqueeze(0)
                bs = kp_source['value'].shape[0]
                predictions_gen = []
                for i in tqdm(range(num_frames)):
                    kp_si = {}
                    kp_si['value'] = kp_source['value'][0].unsqueeze(0)
                    kp_di = {}
                    kp_di['value'] = kp_driving['value'][i].unsqueeze(0)
                    generated = generator(source_img, kp_source=kp_si, kp_driving=kp_di, prompt=emoprompt)
                    predictions_gen.append(
                        (np.transpose(generated['prediction'].data.cpu().numpy(), [0, 2, 3, 1])[0] * 255).astype(np.uint8))

            log_dir = save_dir
            os.makedirs(os.path.join(log_dir, "temp"), exist_ok=True)

            f_name = os.path.basename(img_path[:-4]) + "_" + emotype + "_" + os.path.basename(latent_path_driving)[:-4] + ".mp4"
            video_path = os.path.join(log_dir, "temp", f_name)
            imageio.mimsave(video_path, predictions_gen, fps=25.0)

            save_video = os.path.join(log_dir, f_name)
            cmd = r'ffmpeg -loglevel error -y -i "%s" -i "%s" -vcodec copy -shortest "%s"' % (video_path, audio_path, save_video)
            os.system(cmd)
            os.remove(video_path)

if __name__ == '__main__':
    argparser = argparse.ArgumentParser()
    argparser.add_argument("--save_dir", type=str, default=" ", help="path of the output video")
    argparser.add_argument("--name", type=str, default="deepprompt_eam3d_all_final_313", help="path of the output video")
    argparser.add_argument("--emo", type=str, default="hap", help="emotion type ('ang',  'con',  'dis',  'fea',  'hap',  'neu',  'sad',  'sur')")
    argparser.add_argument("--root_wav", type=str, default='./demo/video_processed/M003_neu_1_001', help="emotion type ('ang',  'con',  'dis',  'fea',  'hap',  'neu',  'sad',  'sur')")
    args = argparser.parse_args()

    root_wav=args.root_wav

    if len(args.name) > 1:
        name = args.name
        print(name)
    test(f'/content/EAT_code/ckpt/deepprompt_eam3d_all_final_313.pth.tar', args.emo, save_dir=f'./demo/output/{name}/')



In [ ]:
#@title trasnformer.py with fixed paths
import torch.nn as nn
import torch
from modules.util import mydownres2Dblock
import numpy as np
from modules.util import AntiAliasInterpolation2d, make_coordinate_grid
from sync_batchnorm import SynchronizedBatchNorm2d as BatchNorm2d
import torch.nn.functional as F
import copy


class PositionalEncoding(nn.Module):

    def __init__(self, d_hid, n_position=200):
        super(PositionalEncoding, self).__init__()

        # Not a parameter
        self.register_buffer('pos_table', self._get_sinusoid_encoding_table(n_position, d_hid))

    def _get_sinusoid_encoding_table(self, n_position, d_hid):
        ''' Sinusoid position encoding table '''
        # TODO: make it with torch instead of numpy

        def get_position_angle_vec(position):
            return [position / np.power(10000, 2 * (hid_j // 2) / d_hid) for hid_j in range(d_hid)]

        sinusoid_table = np.array([get_position_angle_vec(pos_i) for pos_i in range(n_position)])
        sinusoid_table[:, 0::2] = np.sin(sinusoid_table[:, 0::2])  # dim 2i
        sinusoid_table[:, 1::2] = np.cos(sinusoid_table[:, 1::2])  # dim 2i+1

        return torch.FloatTensor(sinusoid_table).unsqueeze(0)

    def forward(self, winsize):
        return self.pos_table[:, :winsize].clone().detach()

def _get_activation_fn(activation):
    """Return an activation function given a string"""
    if activation == "relu":
        return F.relu
    if activation == "gelu":
        return F.gelu
    if activation == "glu":
        return F.glu
    raise RuntimeError(F"activation should be relu/gelu, not {activation}.")

def _get_clones(module, N):
    return nn.ModuleList([copy.deepcopy(module) for i in range(N)])

### light weight transformer encoder
class TransformerST(nn.Module):

    def __init__(self, d_model=128, nhead=8, num_encoder_layers=6,
                 num_decoder_layers=6, dim_feedforward=1024, dropout=0.1,
                 activation="relu", normalize_before=False):
        super().__init__()

        encoder_layer = TransformerEncoderLayer(d_model, nhead, dim_feedforward,
                                                dropout, activation, normalize_before)
        encoder_norm = nn.LayerNorm(d_model) if normalize_before else None
        self.encoder = TransformerEncoder(encoder_layer, num_encoder_layers, encoder_norm)

        self._reset_parameters()

        self.d_model = d_model
        self.nhead = nhead

    def _reset_parameters(self):
        for p in self.parameters():
            if p.dim() > 1:
                nn.init.xavier_uniform_(p)

    def forward(self, src, pos_embed):
        # flatten NxCxHxW to HWxNxC

        src = src.permute(1, 0, 2)
        pos_embed = pos_embed.permute(1, 0, 2)

        memory = self.encoder(src, pos=pos_embed)

        return memory

class TransformerEncoder(nn.Module):

    def __init__(self, encoder_layer, num_layers, norm=None):
        super().__init__()
        self.layers = _get_clones(encoder_layer, num_layers)
        self.num_layers = num_layers
        self.norm = norm

    def forward(self, src, mask = None, src_key_padding_mask = None, pos = None):
        output = src+pos

        for layer in self.layers:
            output = layer(output, src_mask=mask,
                           src_key_padding_mask=src_key_padding_mask, pos=pos)

        if self.norm is not None:
            output = self.norm(output)

        return output

class TransformerDecoder(nn.Module):

    def __init__(self, decoder_layer, num_layers, norm=None, return_intermediate=False):
        super().__init__()
        self.layers = _get_clones(decoder_layer, num_layers)
        self.num_layers = num_layers
        self.norm = norm
        self.return_intermediate = return_intermediate

    def forward(self, tgt, memory,  tgt_mask = None,  memory_mask = None, tgt_key_padding_mask = None,
                memory_key_padding_mask = None,
                pos = None,
                query_pos = None):
        output = tgt+pos+query_pos

        intermediate = []

        for layer in self.layers:
            output = layer(output, memory, tgt_mask=tgt_mask,
                           memory_mask=memory_mask,
                           tgt_key_padding_mask=tgt_key_padding_mask,
                           memory_key_padding_mask=memory_key_padding_mask,
                           pos=pos, query_pos=query_pos)
            if self.return_intermediate:
                intermediate.append(self.norm(output))

        if self.norm is not None:
            output = self.norm(output)
            if self.return_intermediate:
                intermediate.pop()
                intermediate.append(output)

        if self.return_intermediate:
            return torch.stack(intermediate)

        return output.unsqueeze(0)


class Transformer(nn.Module):

    def __init__(self, d_model=128, nhead=8, num_encoder_layers=6,
                 num_decoder_layers=6, dim_feedforward=1024, dropout=0.1,
                 activation="relu", normalize_before=False,
                 return_intermediate_dec=True):
        super().__init__()

        encoder_layer = TransformerEncoderLayer(d_model, nhead, dim_feedforward,
                                                dropout, activation, normalize_before)
        encoder_norm = nn.LayerNorm(d_model) if normalize_before else None
        self.encoder = TransformerEncoder(encoder_layer, num_encoder_layers, encoder_norm)

        decoder_layer = TransformerDecoderLayer(d_model, nhead, dim_feedforward,
                                                dropout, activation, normalize_before)
        decoder_norm = nn.LayerNorm(d_model)
        self.decoder = TransformerDecoder(decoder_layer, num_decoder_layers, decoder_norm,
                                          return_intermediate=return_intermediate_dec)

        self._reset_parameters()

        self.d_model = d_model
        self.nhead = nhead

    def _reset_parameters(self):
        for p in self.parameters():
            if p.dim() > 1:
                nn.init.xavier_uniform_(p)

    def forward(self, src, query_embed, pos_embed):
        # flatten NxCxHxW to HWxNxC

        src = src.permute(1, 0, 2)
        pos_embed = pos_embed.permute(1, 0, 2)
        query_embed = query_embed.permute(1, 0, 2)

        tgt = torch.zeros_like(query_embed)
        memory = self.encoder(src, pos=pos_embed)

        hs = self.decoder(tgt, memory,
                          pos=pos_embed, query_pos=query_embed)
        return hs, memory


class TransformerDeep(nn.Module):

    def __init__(self, d_model=128, nhead=8, num_encoder_layers=6,
                 num_decoder_layers=6, dim_feedforward=1024, dropout=0.1,
                 activation="relu", normalize_before=False,
                 return_intermediate_dec=True):
        super().__init__()

        encoder_layer = TransformerEncoderLayer(d_model, nhead, dim_feedforward,
                                                dropout, activation, normalize_before)
        encoder_norm = nn.LayerNorm(d_model) if normalize_before else None
        self.encoder = TransformerEncoderDeep(encoder_layer, num_encoder_layers, encoder_norm)

        decoder_layer = TransformerDecoderLayer(d_model, nhead, dim_feedforward,
                                                dropout, activation, normalize_before)
        decoder_norm = nn.LayerNorm(d_model)
        self.decoder = TransformerDecoderDeep(decoder_layer, num_decoder_layers, decoder_norm,
                                          return_intermediate=return_intermediate_dec)

        self._reset_parameters()

        self.d_model = d_model
        self.nhead = nhead

    def _reset_parameters(self):
        for p in self.parameters():
            if p.dim() > 1:
                nn.init.xavier_uniform_(p)

    def forward(self, src, query_embed, pos_embed, deepprompt):
        # flatten NxCxHxW to HWxNxC

        # print('src before permute: ', src.shape) # 5, 12, 128
        src = src.permute(1, 0, 2)
        # print('src after permute: ', src.shape) # 12, 5, 128
        pos_embed = pos_embed.permute(1, 0, 2)
        query_embed = query_embed.permute(1, 0, 2)

        tgt = torch.zeros_like(query_embed) # actually is tgt + query_embed
        memory = self.encoder(src, deepprompt, pos=pos_embed)

        hs = self.decoder(tgt, deepprompt, memory,
                          pos=pos_embed, query_pos=query_embed)
        return hs, memory

class TransformerEncoderDeep(nn.Module):

    def __init__(self, encoder_layer, num_layers, norm=None):
        super().__init__()
        self.layers = _get_clones(encoder_layer, num_layers)
        self.num_layers = num_layers
        self.norm = norm

    def forward(self, src, deepprompt, mask = None, src_key_padding_mask = None, pos = None):
        # print('input: ', src.shape) # 12 5 128
        # print('deepprompt:', deepprompt.shape) # 1 6 128
        ### TODO: add deep prompt in encoder
        bs = src.shape[1]
        bbs = deepprompt.shape[0]
        idx=0
        emoprompt = deepprompt[:,idx,:]
        emoprompt = emoprompt.unsqueeze(1).tile(1, bs, 1).reshape(bbs*bs, 128).unsqueeze(0)
        # print(emoprompt.shape) # 1 5 128
        src = torch.cat([src, emoprompt], dim=0)
        # print(src.shape) # 13 5 128
        output = src+pos

        for layer in self.layers:
            output = layer(output, src_mask=mask,
                           src_key_padding_mask=src_key_padding_mask, pos=pos)

            ### deep prompt
            if idx+1 < len(self.layers):
                idx = idx + 1
                # print(idx)
                emoprompt = deepprompt[:,idx,:]
                emoprompt = emoprompt.unsqueeze(1).tile(1, bs, 1).reshape(bbs*bs, 128).unsqueeze(0)
                # print(output.shape) # 13 5 128
                output = torch.cat([output[:-1], emoprompt], dim=0)
                # print(output.shape) # 13 5 128

        if self.norm is not None:
            output = self.norm(output)

        return output

class TransformerDecoderDeep(nn.Module):

    def __init__(self, decoder_layer, num_layers, norm=None, return_intermediate=False):
        super().__init__()
        self.layers = _get_clones(decoder_layer, num_layers)
        self.num_layers = num_layers
        self.norm = norm
        self.return_intermediate = return_intermediate

    def forward(self, tgt, deepprompt, memory, tgt_mask = None,  memory_mask = None, tgt_key_padding_mask = None,
                memory_key_padding_mask = None,
                pos = None,
                query_pos = None):
        # print('input: ', query_pos.shape) 12 5 128
        ### TODO: add deep prompt in encoder
        bs = query_pos.shape[1]
        bbs = deepprompt.shape[0]
        idx=0
        emoprompt = deepprompt[:,idx,:]
        emoprompt = emoprompt.unsqueeze(1).tile(1, bs, 1).reshape(bbs*bs, 128).unsqueeze(0)
        query_pos = torch.cat([query_pos, emoprompt], dim=0)
        # print(query_pos.shape) # 13 5 128
        # print(torch.sum(tgt)) # 0
        output = pos+query_pos

        intermediate = []

        for layer in self.layers:
            output = layer(output, memory, tgt_mask=tgt_mask,
                           memory_mask=memory_mask,
                           tgt_key_padding_mask=tgt_key_padding_mask,
                           memory_key_padding_mask=memory_key_padding_mask,
                           pos=pos, query_pos=query_pos)
            if self.return_intermediate:
                intermediate.append(self.norm(output))

            ### deep prompt
            if idx+1 < len(self.layers):
                idx = idx + 1
                # print(idx)
                emoprompt = deepprompt[:,idx,:]
                emoprompt = emoprompt.unsqueeze(1).tile(1, bs, 1).reshape(bbs*bs, 128).unsqueeze(0)
                # print(output.shape) # 13 5 128
                output = torch.cat([output[:-1], emoprompt], dim=0)
                # print(output.shape) # 13 5 128

        if self.norm is not None:
            output = self.norm(output)
            if self.return_intermediate:
                intermediate.pop()
                intermediate.append(output)

        if self.return_intermediate:
            return torch.stack(intermediate)

        return output.unsqueeze(0)


class TransformerEncoderLayer(nn.Module):

    def __init__(self, d_model, nhead, dim_feedforward=2048, dropout=0.1,
                 activation="relu", normalize_before=False):
        super().__init__()
        self.self_attn = nn.MultiheadAttention(d_model, nhead, dropout=dropout)
        # Implementation of Feedforward model
        self.linear1 = nn.Linear(d_model, dim_feedforward)
        self.dropout = nn.Dropout(dropout)
        self.linear2 = nn.Linear(dim_feedforward, d_model)

        self.norm1 = nn.LayerNorm(d_model)
        self.norm2 = nn.LayerNorm(d_model)
        self.dropout1 = nn.Dropout(dropout)
        self.dropout2 = nn.Dropout(dropout)

        self.activation = _get_activation_fn(activation)
        self.normalize_before = normalize_before

    def with_pos_embed(self, tensor, pos):
        return tensor if pos is None else tensor + pos

    def forward_post(self,
                     src,
                     src_mask = None,
                     src_key_padding_mask = None,
                     pos = None):
        # q = k = self.with_pos_embed(src, pos)
        src2 = self.self_attn(src, src, value=src, attn_mask=src_mask,
                              key_padding_mask=src_key_padding_mask)[0]
        src = src + self.dropout1(src2)
        src = self.norm1(src)
        src2 = self.linear2(self.dropout(self.activation(self.linear1(src))))
        src = src + self.dropout2(src2)
        src = self.norm2(src)
        return src

    def forward_pre(self, src,
                    src_mask = None,
                    src_key_padding_mask = None,
                    pos = None):
        src2 = self.norm1(src)
        # q = k = self.with_pos_embed(src2, pos)
        src2 = self.self_attn(src2, src2, value=src2, attn_mask=src_mask,
                              key_padding_mask=src_key_padding_mask)[0]
        src = src + self.dropout1(src2)
        src2 = self.norm2(src)
        src2 = self.linear2(self.dropout(self.activation(self.linear1(src2))))
        src = src + self.dropout2(src2)
        return src

    def forward(self, src,
                src_mask = None,
                src_key_padding_mask = None,
                pos = None):
        if self.normalize_before:
            return self.forward_pre(src, src_mask, src_key_padding_mask, pos)
        return self.forward_post(src, src_mask, src_key_padding_mask, pos)

class TransformerDecoderLayer(nn.Module):

    def __init__(self, d_model, nhead, dim_feedforward=2048, dropout=0.1,
                 activation="relu", normalize_before=False):
        super().__init__()
        self.self_attn = nn.MultiheadAttention(d_model, nhead, dropout=dropout)
        self.multihead_attn = nn.MultiheadAttention(d_model, nhead, dropout=dropout)
        # Implementation of Feedforward model
        self.linear1 = nn.Linear(d_model, dim_feedforward)
        self.dropout = nn.Dropout(dropout)
        self.linear2 = nn.Linear(dim_feedforward, d_model)

        self.norm1 = nn.LayerNorm(d_model)
        self.norm2 = nn.LayerNorm(d_model)
        self.norm3 = nn.LayerNorm(d_model)
        self.dropout1 = nn.Dropout(dropout)
        self.dropout2 = nn.Dropout(dropout)
        self.dropout3 = nn.Dropout(dropout)

        self.activation = _get_activation_fn(activation)
        self.normalize_before = normalize_before

    def with_pos_embed(self, tensor, pos):
        return tensor if pos is None else tensor + pos

    def forward_post(self, tgt, memory,
                     tgt_mask = None,
                     memory_mask = None,
                     tgt_key_padding_mask = None,
                     memory_key_padding_mask = None,
                     pos = None,
                     query_pos = None):
        # q = k = self.with_pos_embed(tgt, query_pos)
        tgt2 = self.self_attn(tgt, tgt, value=tgt, attn_mask=tgt_mask,
                              key_padding_mask=tgt_key_padding_mask)[0]
        tgt = tgt + self.dropout1(tgt2)
        tgt = self.norm1(tgt)
        tgt2 = self.multihead_attn(query=tgt,
                                   key=memory,
                                   value=memory, attn_mask=memory_mask,
                                   key_padding_mask=memory_key_padding_mask)[0]
        tgt = tgt + self.dropout2(tgt2)
        tgt = self.norm2(tgt)
        tgt2 = self.linear2(self.dropout(self.activation(self.linear1(tgt))))
        tgt = tgt + self.dropout3(tgt2)
        tgt = self.norm3(tgt)
        return tgt

    def forward_pre(self, tgt, memory,
                    tgt_mask = None,
                    memory_mask = None,
                    tgt_key_padding_mask = None,
                    memory_key_padding_mask = None,
                    pos = None,
                    query_pos = None):
        tgt2 = self.norm1(tgt)
        # q = k = self.with_pos_embed(tgt2, query_pos)
        tgt2 = self.self_attn(tgt2, tgt2, value=tgt2, attn_mask=tgt_mask,
                              key_padding_mask=tgt_key_padding_mask)[0]
        tgt = tgt + self.dropout1(tgt2)
        tgt2 = self.norm2(tgt)
        tgt2 = self.multihead_attn(query=tgt2,
                                   key=memory,
                                   value=memory, attn_mask=memory_mask,
                                   key_padding_mask=memory_key_padding_mask)[0]
        tgt = tgt + self.dropout2(tgt2)
        tgt2 = self.norm3(tgt)
        tgt2 = self.linear2(self.dropout(self.activation(self.linear1(tgt2))))
        tgt = tgt + self.dropout3(tgt2)
        return tgt

    def forward(self, tgt, memory,
                tgt_mask = None,
                memory_mask = None,
                tgt_key_padding_mask = None,
                memory_key_padding_mask = None,
                pos = None,
                query_pos = None):
        if self.normalize_before:
            return self.forward_pre(tgt, memory, tgt_mask, memory_mask,
                                    tgt_key_padding_mask, memory_key_padding_mask, pos, query_pos)
        return self.forward_post(tgt, memory, tgt_mask, memory_mask,
                                 tgt_key_padding_mask, memory_key_padding_mask, pos, query_pos)

from Utils.JDC.model import JDCNet
from modules.audioencoder import AudioEncoder, MappingNetwork, StyleEncoder, AdaIN, EAModule

def headpose_pred_to_degree(pred):
    device = pred.device
    idx_tensor = [idx for idx in range(66)]
    idx_tensor = torch.FloatTensor(idx_tensor).to(device)
    pred = F.softmax(pred, dim=1)
    degree = torch.sum(pred*idx_tensor, axis=1)
    # degree = F.one_hot(degree.to(torch.int64), num_classes=66)
    return degree

def get_rotation_matrix(yaw, pitch, roll):
    yaw = yaw / 180 * 3.14
    pitch = pitch / 180 * 3.14
    roll = roll / 180 * 3.14

    roll = roll.unsqueeze(1)
    pitch = pitch.unsqueeze(1)
    yaw = yaw.unsqueeze(1)

    pitch_mat = torch.cat([torch.ones_like(pitch), torch.zeros_like(pitch), torch.zeros_like(pitch),
                          torch.zeros_like(pitch), torch.cos(pitch), -torch.sin(pitch),
                          torch.zeros_like(pitch), torch.sin(pitch), torch.cos(pitch)], dim=1)

    pitch_mat = pitch_mat.view(pitch_mat.shape[0], 3, 3)

    yaw_mat = torch.cat([torch.cos(yaw), torch.zeros_like(yaw), torch.sin(yaw),
                           torch.zeros_like(yaw), torch.ones_like(yaw), torch.zeros_like(yaw),
                           -torch.sin(yaw), torch.zeros_like(yaw), torch.cos(yaw)], dim=1)
    yaw_mat = yaw_mat.view(yaw_mat.shape[0], 3, 3)

    roll_mat = torch.cat([torch.cos(roll), -torch.sin(roll), torch.zeros_like(roll),
                         torch.sin(roll), torch.cos(roll), torch.zeros_like(roll),
                         torch.zeros_like(roll), torch.zeros_like(roll), torch.ones_like(roll)], dim=1)
    roll_mat = roll_mat.view(roll_mat.shape[0], 3, 3)

    rot_mat = torch.einsum('bij,bjk,bkm->bim', pitch_mat, yaw_mat, roll_mat)

    return yaw, pitch, roll, yaw_mat.view(yaw_mat.shape[0], 9), pitch_mat.view(pitch_mat.shape[0], 9), roll_mat.view(roll_mat.shape[0], 9), rot_mat.view(rot_mat.shape[0], 9)

class Audio2kpTransformerBBoxQDeep(nn.Module):
    def __init__(self, embedding_dim, num_kp, num_w, face_adain=False):
        super(Audio2kpTransformerBBoxQDeep, self).__init__()
        self.embedding_dim = embedding_dim
        self.num_kp = num_kp
        self.num_w = num_w


        self.embedding = nn.Embedding(41, embedding_dim)

        self.face_shrink = nn.Linear(240, 32)
        self.hp_extractor = nn.Linear(45, 128)

        self.pos_enc = PositionalEncoding(128,20)
        input_dim = 1

        self.decode_dim = 64
        self.audio_embedding = nn.Sequential(  # n x 29 x 16
            nn.Conv1d(29, 32, kernel_size=3, stride=2,
                      padding=1, bias=True),  # n x 32 x 8
            nn.LeakyReLU(0.02, True),
            nn.Conv1d(32, 32, kernel_size=3, stride=2,
                      padding=1, bias=True),  # n x 32 x 4
            nn.LeakyReLU(0.02, True),
            nn.Conv1d(32, 64, kernel_size=3, stride=2,
                      padding=1, bias=True),  # n x 64 x 2
            nn.LeakyReLU(0.02, True),
            nn.Conv1d(64, 64, kernel_size=3, stride=2,
                      padding=1, bias=True),  # n x 64 x 1
            nn.LeakyReLU(0.02, True),
        )
        self.encoder_fc1 = nn.Sequential(
            nn.Linear(192, 128),
            nn.LeakyReLU(0.02, True),
            nn.Linear(128, 128),
        )

        self.audio_embedding2 = nn.Sequential(nn.Conv2d(1, 8, (3, 17), stride=(1, 1), padding=(1, 0)),
                                            #  nn.GroupNorm(4, 8, affine=True),
                                             BatchNorm2d(8),
                                             nn.ReLU(inplace=True),
                                             nn.Conv2d(8, 32, (13, 13), stride=(1, 1), padding=(6, 6)))

        self.audioencoder = AudioEncoder(dim_in=64, style_dim=128, max_conv_dim=512, w_hpf=0, F0_channel=256)
        # self.mappingnet = MappingNetwork(latent_dim=16, style_dim=128, num_domains=8, hidden_dim=512)
        # self.stylenet = StyleEncoder(dim_in=64, style_dim=64, num_domains=8, max_conv_dim=512)
        self.face_adain = face_adain
        if self.face_adain:
            self.fadain = AdaIN(style_dim=128, num_features=32)
        # norm = 'layer_2d' #
        norm = 'batch'

        self.decodefeature_extract = nn.Sequential(mydownres2Dblock(self.decode_dim,32, normalize = norm),
                                             mydownres2Dblock(32,48, normalize = norm),
                                             mydownres2Dblock(48,64, normalize = norm),
                                             mydownres2Dblock(64,96, normalize = norm),
                                             mydownres2Dblock(96,128, normalize = norm),
                                             nn.AvgPool2d(2))

        self.feature_extract = nn.Sequential(mydownres2Dblock(input_dim,32),
                                             mydownres2Dblock(32,64),
                                             mydownres2Dblock(64,128),
                                             mydownres2Dblock(128,128),
                                             mydownres2Dblock(128,128),
                                             nn.AvgPool2d(2))
        self.transformer = Transformer()
        self.kp = nn.Linear(128, 32)

        # for m in self.modules():
            # if isinstance(m, nn.Conv2d):
            #     # nn.init.kaiming_normal_(m.weight, mode='fan_out', nonlinearity='relu')
            #     nn.init.xavier_uniform_(m.weight, gain=1)

            # if isinstance(m, nn.Linear):
            #     # trunc_normal_(m.weight, std=.03)
            #     nn.init.xavier_uniform_(m.weight, gain=1)
            #     if isinstance(m, nn.Linear) and m.bias is not None:
            #         nn.init.constant_(m.bias, 0)

        F0_path = './Utils/JDC/bst.t7'
        F0_model = JDCNet(num_class=1, seq_len=32)
        params = torch.load(F0_path, map_location='cpu')['net']
        F0_model.load_state_dict(params)
        self.f0_model = F0_model

    def rotation_and_translation(self, headpose, bbs, bs):
        # print(headpose['roll'].shape, headpose['yaw'].shape, headpose['pitch'].shape, headpose['t'].shape)

        yaw = headpose_pred_to_degree(headpose['yaw'].reshape(bbs*bs, -1))
        pitch = headpose_pred_to_degree(headpose['pitch'].reshape(bbs*bs, -1))
        roll = headpose_pred_to_degree(headpose['roll'].reshape(bbs*bs, -1))
        yaw_2, pitch_2, roll_2, yaw_v, pitch_v, roll_v, rot_v = get_rotation_matrix(yaw, pitch, roll)
        t = headpose['t'].reshape(bbs*bs, -1)
        # hp = torch.cat([yaw, pitch, roll, yaw_v, pitch_v, roll_v, t], dim=1)
        hp = torch.cat([yaw.unsqueeze(1), pitch.unsqueeze(1), roll.unsqueeze(1), yaw_2, pitch_2, roll_2, yaw_v, pitch_v, roll_v, rot_v, t], dim=1)
        # hp = torch.cat([yaw, pitch, roll, torch.sin(yaw), torch.sin(pitch), torch.sin(roll), torch.cos(yaw), torch.cos(pitch), torch.cos(roll), t], dim=1)
        return hp

    def forward(self, x, initial_kp = None, return_strg=False, emoprompt=None, hp=None, side=False):
        bbs, bs, seqlen, _, _ = x['deep'].shape
        # ph = x["pho"].reshape(bbs*bs*seqlen, 1)
        if hp is None:
            hp = self.rotation_and_translation(x['he_driving'], bbs, bs)
        hp = self.hp_extractor(hp)

        pose_feature = x["pose"].reshape(bbs*bs*seqlen,1,64,64)
        # pose_feature = self.down_pose(pose).contiguous()
        ### phoneme input feature
        # phoneme_embedding = self.embedding(ph.long())
        # phoneme_embedding = phoneme_embedding.reshape(bbs*bs*seqlen, 1, 16, 16)
        # phoneme_embedding = F.interpolate(phoneme_embedding, scale_factor=4)
        # input_feature = torch.cat((pose_feature, phoneme_embedding), dim=1)
        # print('input_feature: ', input_feature.shape)
        # input_feature = phoneme_embedding

        audio = x['deep'].reshape(bbs*bs*seqlen, 16, 29).permute(0, 2, 1)
        deep_feature = self.audio_embedding(audio).squeeze(-1)# ([264, 32, 16, 16])
        # print(deep_feature.shape)

        input_feature = pose_feature
        # print(input_feature.shape)
        # assert(0)
        input_feature = self.feature_extract(input_feature).reshape(bbs*bs*seqlen, 128)
        input_feature = torch.cat([input_feature, deep_feature], dim=1)
        input_feature = self.encoder_fc1(input_feature).reshape(bbs*bs, seqlen, 128)
        # phoneme_embedding = self.phoneme_shrink(phoneme_embedding.squeeze(1))# 24*11, 128
        input_feature = torch.cat([input_feature, hp.unsqueeze(1)], dim=1)

        ### decode audio feature
        ### use iteration to avoid batchnorm2d in different audio sequence
        decoder_features = []
        for i in range(bbs):
            F0 = self.f0_model.get_feature_GAN(x['mel'][i].reshape(bs, 1, 80, seqlen))
            if emoprompt is None:
                audio_feature = (self.audioencoder(x['mel'][i].reshape(bs, 1, 80, seqlen), s=None, masks=None, F0=F0))
            else:
                audio_feature = (self.audioencoder(x['mel'][i].reshape(bs, 1, 80, seqlen), s=emoprompt[i].unsqueeze(0), masks=None, F0=F0))
            audio2 = torch.permute(audio_feature, (0, 3, 1, 2)).reshape(bs*seqlen, 1, 64, 80)
            decoder_feature = self.audio_embedding2(audio2)

            # decoder_feature = torch.cat([decoder_feature, audio2], dim=1)
            # decoder_feature = F.interpolate(decoder_feature, scale_factor=2)# ([264, 35, 64, 64])
            face_map = initial_kp["prediction_map"][i].reshape(15*16, 64*64).permute(1, 0).reshape(64*64, 15*16)
            feature_map = self.face_shrink(face_map).permute(1, 0).reshape(1, 32, 64, 64)
            if self.face_adain:
                feature_map = self.fadain(feature_map, emoprompt)
            decoder_feature = self.decodefeature_extract(torch.cat(
                (decoder_feature,
                feature_map.repeat(bs, seqlen, 1, 1, 1).reshape(bs * seqlen, 32, 64, 64)),
                dim=1)).reshape(bs, seqlen, 128)
            decoder_features.append(decoder_feature)
        decoder_feature = torch.cat(decoder_features, dim=0)

        decoder_feature = torch.cat([decoder_feature, hp.unsqueeze(1)], dim=1)

        # decoder_feature = torch.cat([decoder_feature], dim=1)

        # a2kp transformer
        # position embedding
        if emoprompt is None:
            posi_em = self.pos_enc(self.num_w*2+1+1) # 11 + headpose token
        else:
            posi_em = self.pos_enc(self.num_w*2+1+1+1) # 11 + headpose token + emotion prompt
            emoprompt = emoprompt.unsqueeze(1).tile(1, bs, 1).reshape(bbs*bs, 128).unsqueeze(1)
            input_feature = torch.cat([input_feature, emoprompt], dim=1)
            decoder_feature = torch.cat([decoder_feature, emoprompt], dim=1)
        out = {}
        output_feature, memory = self.transformer(input_feature, decoder_feature, posi_em, )
        output_feature = output_feature[-1, self.num_w] # returned intermediate output [6, 13, bbs*bs, 128]
        out["emo"] = self.kp(output_feature)
        if side:
            input_st = {}
            input_st['hp'] = hp
            input_st['decoder_feature'] = decoder_feature
            input_st['memory'] = memory
            return out, input_st
        else:
            return out


class Audio2kpTransformerBBoxQDeepPrompt(nn.Module):
    def __init__(self, embedding_dim, num_kp, num_w, face_ea=False):
        super(Audio2kpTransformerBBoxQDeepPrompt, self).__init__()
        self.embedding_dim = embedding_dim
        self.num_kp = num_kp
        self.num_w = num_w


        self.embedding = nn.Embedding(41, embedding_dim)

        self.face_shrink = nn.Linear(240, 32)
        self.hp_extractor = nn.Linear(45, 128)

        self.pos_enc = PositionalEncoding(128,20)
        input_dim = 1

        self.decode_dim = 64
        self.audio_embedding = nn.Sequential(  # n x 29 x 16
            nn.Conv1d(29, 32, kernel_size=3, stride=2,
                      padding=1, bias=True),  # n x 32 x 8
            nn.LeakyReLU(0.02, True),
            nn.Conv1d(32, 32, kernel_size=3, stride=2,
                      padding=1, bias=True),  # n x 32 x 4
            nn.LeakyReLU(0.02, True),
            nn.Conv1d(32, 64, kernel_size=3, stride=2,
                      padding=1, bias=True),  # n x 64 x 2
            nn.LeakyReLU(0.02, True),
            nn.Conv1d(64, 64, kernel_size=3, stride=2,
                      padding=1, bias=True),  # n x 64 x 1
            nn.LeakyReLU(0.02, True),
        )
        self.encoder_fc1 = nn.Sequential(
            nn.Linear(192, 128),
            nn.LeakyReLU(0.02, True),
            nn.Linear(128, 128),
        )

        self.audio_embedding2 = nn.Sequential(nn.Conv2d(1, 8, (3, 17), stride=(1, 1), padding=(1, 0)),
                                            #  nn.GroupNorm(4, 8, affine=True),
                                             BatchNorm2d(8),
                                             nn.ReLU(inplace=True),
                                             nn.Conv2d(8, 32, (13, 13), stride=(1, 1), padding=(6, 6)))

        self.audioencoder = AudioEncoder(dim_in=64, style_dim=128, max_conv_dim=512, w_hpf=0, F0_channel=256)
        self.face_ea = face_ea
        if self.face_ea:
            self.fea = EAModule(style_dim=128, num_features=32)
        norm = 'batch'

        self.decodefeature_extract = nn.Sequential(mydownres2Dblock(self.decode_dim,32, normalize = norm),
                                             mydownres2Dblock(32,48, normalize = norm),
                                             mydownres2Dblock(48,64, normalize = norm),
                                             mydownres2Dblock(64,96, normalize = norm),
                                             mydownres2Dblock(96,128, normalize = norm),
                                             nn.AvgPool2d(2))

        self.feature_extract = nn.Sequential(mydownres2Dblock(input_dim,32),
                                             mydownres2Dblock(32,64),
                                             mydownres2Dblock(64,128),
                                             mydownres2Dblock(128,128),
                                             mydownres2Dblock(128,128),
                                             nn.AvgPool2d(2))
        self.transformer = TransformerDeep()
        self.kp = nn.Linear(128, 32)

        F0_path = '/content/EAT_code/Utils/JDC/bst.t7'
        F0_model = JDCNet(num_class=1, seq_len=32)
        params = torch.load(F0_path, map_location='cpu')['net']
        F0_model.load_state_dict(params)
        self.f0_model = F0_model

    def rotation_and_translation(self, headpose, bbs, bs):
        yaw = headpose_pred_to_degree(headpose['yaw'].reshape(bbs*bs, -1))
        pitch = headpose_pred_to_degree(headpose['pitch'].reshape(bbs*bs, -1))
        roll = headpose_pred_to_degree(headpose['roll'].reshape(bbs*bs, -1))
        yaw_2, pitch_2, roll_2, yaw_v, pitch_v, roll_v, rot_v = get_rotation_matrix(yaw, pitch, roll)
        t = headpose['t'].reshape(bbs*bs, -1)
        hp = torch.cat([yaw.unsqueeze(1), pitch.unsqueeze(1), roll.unsqueeze(1), yaw_2, pitch_2, roll_2, yaw_v, pitch_v, roll_v, rot_v, t], dim=1)
        return hp

    def forward(self, x, initial_kp = None, return_strg=False, emoprompt=None, deepprompt=None, hp=None, side=False):
        bbs, bs, seqlen, _, _ = x['deep'].shape
        # ph = x["pho"].reshape(bbs*bs*seqlen, 1)
        if hp is None:
            hp = self.rotation_and_translation(x['he_driving'], bbs, bs)
        hp = self.hp_extractor(hp)

        pose_feature = x["pose"].reshape(bbs*bs*seqlen,1,64,64)

        audio = x['deep'].reshape(bbs*bs*seqlen, 16, 29).permute(0, 2, 1)
        deep_feature = self.audio_embedding(audio).squeeze(-1)# ([264, 32, 16, 16])

        input_feature = pose_feature
        input_feature = self.feature_extract(input_feature).reshape(bbs*bs*seqlen, 128)
        input_feature = torch.cat([input_feature, deep_feature], dim=1)
        input_feature = self.encoder_fc1(input_feature).reshape(bbs*bs, seqlen, 128)
        input_feature = torch.cat([input_feature, hp.unsqueeze(1)], dim=1)

        ### decode audio feature
        ### use iteration to avoid batchnorm2d in different audio sequence
        decoder_features = []
        for i in range(bbs):
            F0 = self.f0_model.get_feature_GAN(x['mel'][i].reshape(bs, 1, 80, seqlen))
            if emoprompt is None:
                audio_feature = (self.audioencoder(x['mel'][i].reshape(bs, 1, 80, seqlen), s=None, masks=None, F0=F0))
            else:
                audio_feature = (self.audioencoder(x['mel'][i].reshape(bs, 1, 80, seqlen), s=emoprompt[i].unsqueeze(0), masks=None, F0=F0))
            audio2 = torch.permute(audio_feature, (0, 3, 1, 2)).reshape(bs*seqlen, 1, 64, 80)
            decoder_feature = self.audio_embedding2(audio2)

            face_map = initial_kp["prediction_map"][i].reshape(15*16, 64*64).permute(1, 0).reshape(64*64, 15*16)
            face_feature_map = self.face_shrink(face_map).permute(1, 0).reshape(1, 32, 64, 64)
            if self.face_ea:
                face_feature_map = self.fea(face_feature_map, emoprompt)
            decoder_feature = self.decodefeature_extract(torch.cat(
                (decoder_feature,
                face_feature_map.repeat(bs, seqlen, 1, 1, 1).reshape(bs * seqlen, 32, 64, 64)),
                dim=1)).reshape(bs, seqlen, 128)
            decoder_features.append(decoder_feature)
        decoder_feature = torch.cat(decoder_features, dim=0)

        decoder_feature = torch.cat([decoder_feature, hp.unsqueeze(1)], dim=1)

        # a2kp transformer
        # position embedding
        if emoprompt is None:
            posi_em = self.pos_enc(self.num_w*2+1+1) # 11 + headpose token
        else:
            posi_em = self.pos_enc(self.num_w*2+1+1+1) # 11 + headpose token + deep emotion prompt
        out = {}
        output_feature, memory = self.transformer(input_feature, decoder_feature, posi_em, deepprompt)
        output_feature = output_feature[-1, self.num_w] # returned intermediate output [6, 13, bbs*bs, 128]
        out["emo"] = self.kp(output_feature)
        if side:
            input_st = {}
            input_st['hp'] = hp
            input_st['face_feature_map'] = face_feature_map
            input_st['bs'] = bs
            input_st['bbs'] = bbs
            return out, input_st
        else:
            return out




In [ ]:
#@title deepspeechfeatures.py fixed

"""
    DeepSpeech features processing routines.
    NB: Based on VOCA code. See the corresponding license restrictions.
"""

__all__ = ['conv_audios_to_deepspeech']

import numpy as np
import warnings
import resampy
from scipy.io import wavfile
from python_speech_features import mfcc
import tensorflow as tf


def conv_audios_to_deepspeech(audios,
                              out_files,
                              num_frames_info,
                              deepspeech_pb_path,
                              audio_window_size=16,
                              audio_window_stride=1):
    """
    Convert list of audio files into files with DeepSpeech features.

    Parameters
    ----------
    audios : list of str or list of None
        Paths to input audio files.
    out_files : list of str
        Paths to output files with DeepSpeech features.
    num_frames_info : list of int
        List of numbers of frames.
    deepspeech_pb_path : str
        Path to DeepSpeech 0.1.0 frozen model.
    audio_window_size : int, default 16
        Audio window size.
    audio_window_stride : int, default 1
        Audio window stride.
    """
    graph, logits_ph, input_node_ph, input_lengths_ph = prepare_deepspeech_net(deepspeech_pb_path)

    with tf.compat.v1.Session(graph=graph) as sess:
        for audio_file_path, out_file_path, num_frames in zip(audios, out_files, num_frames_info):
            audio_sample_rate, audio = wavfile.read(audio_file_path)
            if audio.ndim != 1:
                warnings.warn("Audio has multiple channels, the first channel is used")
                audio = audio[:, 0]
            ds_features = pure_conv_audio_to_deepspeech(
                audio=audio,
                audio_sample_rate=audio_sample_rate,
                audio_window_size=audio_window_size,
                audio_window_stride=audio_window_stride,
                num_frames=num_frames,
                net_fn=lambda x: sess.run(
                    logits_ph,
                    feed_dict={
                        input_node_ph: x[np.newaxis, ...],
                        input_lengths_ph: [x.shape[0]]}))
            np.save(out_file_path, ds_features)


# data_util/deepspeech_features/deepspeech_features.py
def prepare_deepspeech_net(deepspeech_pb_path):
    # Load graph and place_holders:
    with tf.io.gfile.GFile(deepspeech_pb_path, "rb") as f:
        graph_def = tf.compat.v1.GraphDef()
        graph_def.ParseFromString(f.read())

    graph = tf.compat.v1.get_default_graph()

    tf.import_graph_def(graph_def, name="deepspeech")
    # check all graphs
    # print('~'*50, [tensor for tensor in graph._nodes_by_name], '~'*50)
    # print('~'*50, [tensor.name for tensor in graph.get_operations()], '~'*50)
    # i modified
    logits_ph = graph.get_tensor_by_name("logits:0")
    input_node_ph = graph.get_tensor_by_name("input_node:0")
    input_lengths_ph = graph.get_tensor_by_name("input_lengths:0")
    # original
    # logits_ph = graph.get_tensor_by_name("deepspeech/logits:0")
    # input_node_ph = graph.get_tensor_by_name("deepspeech/input_node:0")
    # input_lengths_ph = graph.get_tensor_by_name("deepspeech/input_lengths:0")

    return graph, logits_ph, input_node_ph, input_lengths_ph


def pure_conv_audio_to_deepspeech(audio,
                                  audio_sample_rate,
                                  audio_window_size,
                                  audio_window_stride,
                                  num_frames,
                                  net_fn):
    """
    Core routine for converting audion into DeepSpeech features.

    Parameters
    ----------
    audio : np.array
        Audio data.
    audio_sample_rate : int
        Audio sample rate.
    audio_window_size : int
        Audio window size.
    audio_window_stride : int
        Audio window stride.
    num_frames : int or None
        Numbers of frames.
    net_fn : func
        Function for DeepSpeech model call.

    Returns
    -------
    np.array
        DeepSpeech features.
    """
    target_sample_rate = 16000
    if audio_sample_rate != target_sample_rate:
        resampled_audio = resampy.resample(
            x=audio.astype(np.float),
            sr_orig=audio_sample_rate,
            sr_new=target_sample_rate)
    else:
        resampled_audio = audio.astype(np.float32)
    input_vector = conv_audio_to_deepspeech_input_vector(
        audio=resampled_audio.astype(np.int16),
        sample_rate=target_sample_rate,
        num_cepstrum=26,
        num_context=9)

    network_output = net_fn(input_vector)

    deepspeech_fps = 50
    video_fps = 60
    audio_len_s = float(audio.shape[0]) / audio_sample_rate
    if num_frames is None:
        num_frames = int(round(audio_len_s * video_fps))
    else:
        video_fps = num_frames / audio_len_s
    network_output = interpolate_features(
        features=network_output[:, 0],
        input_rate=deepspeech_fps,
        output_rate=video_fps,
        output_len=num_frames)

    # Make windows:
    zero_pad = np.zeros((int(audio_window_size / 2), network_output.shape[1]))
    network_output = np.concatenate((zero_pad, network_output, zero_pad), axis=0)
    windows = []
    for window_index in range(0, network_output.shape[0] - audio_window_size, audio_window_stride):
        windows.append(network_output[window_index:window_index + audio_window_size])

    return np.array(windows)


def conv_audio_to_deepspeech_input_vector(audio,
                                          sample_rate,
                                          num_cepstrum,
                                          num_context):
    """
    Convert audio raw data into DeepSpeech input vector.

    Parameters
    ----------
    audio : np.array
        Audio data.
    audio_sample_rate : int
        Audio sample rate.
    num_cepstrum : int
        Number of cepstrum.
    num_context : int
        Number of context.

    Returns
    -------
    np.array
        DeepSpeech input vector.
    """
    # Get mfcc coefficients:
    features = mfcc(
        signal=audio,
        samplerate=sample_rate,
        numcep=num_cepstrum)

    # We only keep every second feature (BiRNN stride = 2):
    features = features[::2]

    # One stride per time step in the input:
    num_strides = len(features)

    # Add empty initial and final contexts:
    empty_context = np.zeros((num_context, num_cepstrum), dtype=features.dtype)
    features = np.concatenate((empty_context, features, empty_context))

    # Create a view into the array with overlapping strides of size
    # numcontext (past) + 1 (present) + numcontext (future):
    window_size = 2 * num_context + 1
    train_inputs = np.lib.stride_tricks.as_strided(
        features,
        shape=(num_strides, window_size, num_cepstrum),
        strides=(features.strides[0], features.strides[0], features.strides[1]),
        writeable=False)

    # Flatten the second and third dimensions:
    train_inputs = np.reshape(train_inputs, [num_strides, -1])

    train_inputs = np.copy(train_inputs)
    train_inputs = (train_inputs - np.mean(train_inputs)) / np.std(train_inputs)

    return train_inputs


def interpolate_features(features,
                         input_rate,
                         output_rate,
                         output_len):
    """
    Interpolate DeepSpeech features.

    Parameters
    ----------
    features : np.array
        DeepSpeech features.
    input_rate : int
        input rate (FPS).
    output_rate : int
        Output rate (FPS).
    output_len : int
        Output data length.

    Returns
    -------
    np.array
        Interpolated data.
    """
    input_len = features.shape[0]
    num_features = features.shape[1]
    input_timestamps = np.arange(input_len) / float(input_rate)
    output_timestamps = np.arange(output_len) / float(output_rate)
    output_features = np.zeros((output_len, num_features))
    for feature_idx in range(num_features):
        output_features[:, feature_idx] = np.interp(
            x=output_timestamps,
            xp=input_timestamps,
            fp=features[:, feature_idx])
    return output_features


In [ ]:
#@title deepspeechstore fixed

"""
    Routines for loading DeepSpeech model.
"""

__all__ = ['get_deepspeech_model_file']

import os
import zipfile
import logging
import hashlib


deepspeech_features_repo_url = 'https://github.com/osmr/deepspeech_features'


def get_deepspeech_model_file(local_model_store_dir_path=os.path.join("~", "/content/EAT_code/tensorflow", "models")):
    """
    Return location for the pretrained on local file system. This function will download from online model zoo when
    model cannot be found or has mismatch. The root directory will be created if it doesn't exist.

    Parameters
    ----------
    local_model_store_dir_path : str, default $TENSORFLOW_HOME/models
        Location for keeping the model parameters.

    Returns
    -------
    file_path
        Path to the requested pretrained model file.
    """
    sha1_hash = "b90017e816572ddce84f5843f1fa21e6a377975e"
    file_name = "deepspeech-0_1_0-b90017e8.pb"
    local_model_store_dir_path = os.path.expanduser(local_model_store_dir_path)
    file_path = os.path.join(local_model_store_dir_path, file_name)
    if os.path.exists(file_path):
        if _check_sha1(file_path, sha1_hash):
            return file_path
        else:
            logging.warning("Mismatch in the content of model file detected. Downloading again.")
    else:
        logging.info("Model file not found. Downloading to {}.".format(file_path))

    if not os.path.exists(local_model_store_dir_path):
        os.makedirs(local_model_store_dir_path)

    zip_file_path = file_path + ".zip"
    _download(
        url="{repo_url}/releases/download/{repo_release_tag}/{file_name}.zip".format(
            repo_url=deepspeech_features_repo_url,
            repo_release_tag="v0.0.1",
            file_name=file_name),
        path=zip_file_path,
        overwrite=False)
    with zipfile.ZipFile(zip_file_path) as zf:
        zf.extractall(local_model_store_dir_path)
    os.remove(zip_file_path)

    if _check_sha1(file_path, sha1_hash):
        return file_path
    else:
        raise ValueError("Downloaded file has different hash. Please try again.")


def _download(url, path=None, overwrite=False, sha1_hash=None, retries=5, verify_ssl=True):
    """
    Download an given URL

    Parameters
    ----------
    url : str
        URL to download
    path : str, optional
        Destination path to store downloaded file. By default stores to the
        current directory with same name as in url.
    overwrite : bool, optional
        Whether to overwrite destination file if already exists.
    sha1_hash : str, optional
        Expected sha1 hash in hexadecimal digits. Will ignore existing file when hash is specified
        but doesn't match.
    retries : integer, default 5
        The number of times to attempt the download in case of failure or non 200 return codes
    verify_ssl : bool, default True
        Verify SSL certificates.

    Returns
    -------
    str
        The file path of the downloaded file.
    """
    import warnings
    try:
        import requests
    except ImportError:
        class requests_failed_to_import(object):
            pass
        requests = requests_failed_to_import

    if path is None:
        fname = url.split("/")[-1]
        # Empty filenames are invalid
        assert fname, "Can't construct file-name from this URL. Please set the `path` option manually."
    else:
        path = os.path.expanduser(path)
        if os.path.isdir(path):
            fname = os.path.join(path, url.split("/")[-1])
        else:
            fname = path
    assert retries >= 0, "Number of retries should be at least 0"

    if not verify_ssl:
        warnings.warn(
            "Unverified HTTPS request is being made (verify_ssl=False). "
            "Adding certificate verification is strongly advised.")

    if overwrite or not os.path.exists(fname) or (sha1_hash and not _check_sha1(fname, sha1_hash)):
        dirname = os.path.dirname(os.path.abspath(os.path.expanduser(fname)))
        if not os.path.exists(dirname):
            os.makedirs(dirname)
        while retries + 1 > 0:
            # Disable pyling too broad Exception
            # pylint: disable=W0703
            try:
                print("Downloading {} from {}...".format(fname, url))
                #r = requests.get(url, stream=True, verify=verify_ssl)
                #if r.status_code != 200:
                #    raise RuntimeError("Failed downloading url {}".format(url))
                #with open(fname, "wb") as f:
                #    for chunk in r.iter_content(chunk_size=1024):
                #        if chunk:  # filter out keep-alive new chunks
                #            f.write(chunk)
                if sha1_hash and not _check_sha1(fname, sha1_hash):
                    raise UserWarning("File {} is downloaded but the content hash does not match."
                                      " The repo may be outdated or download may be incomplete. "
                                      "If the `repo_url` is overridden, consider switching to "
                                      "the default repo.".format(fname))
                break
            except Exception as e:
                retries -= 1
                if retries <= 0:
                    raise e
                else:
                    print("download failed, retrying, {} attempt{} left"
                          .format(retries, "s" if retries > 1 else ""))

    return fname


def _check_sha1(filename, sha1_hash):
    """
    Check whether the sha1 hash of the file content matches the expected hash.

    Parameters
    ----------
    filename : str
        Path to the file.
    sha1_hash : str
        Expected sha1 hash in hexadecimal digits.

    Returns
    -------
    bool
        Whether the file content matches the expected hash.
    """
    sha1 = hashlib.sha1()
    with open(filename, "rb") as f:
        while True:
            data = f.read(1048576)
            if not data:
                break
            sha1.update(data)

    return sha1.hexdigest() == sha1_hash


In [ ]:
!zip -r EAT_code /content/EAT_code